### Case Study : Stock market data from yahoo-finance for a few stocks

In [1]:
import yfinance as yf
import pandas as pd

In [2]:
# Function to fetch stock data from Yahoo Finance for multiple tickers
def fetch_multiple_stock_data(tickers, start_date, end_date):
    stock_data = pd.DataFrame()
    for ticker in tickers:
        data = yf.download(ticker, start=start_date, end=end_date)
        data['Ticker'] = ticker  # Add ticker as a column
        stock_data = pd.concat([stock_data, data])
    return stock_data

# Function to calculate returns for multiple stocks
def calculate_returns(stock_data):
    stock_data['Daily_Returns'] = stock_data.groupby('Ticker')['Adj Close'].pct_change()
    return stock_data

# Function to calculate risk measures for multiple stocks
def calculate_risk(stock_data):
    risk_measures = stock_data.groupby('Ticker')['Daily_Returns'].agg(['std', 'var'])
    return risk_measures


In [3]:
# Main function
def stocks(ticker_list,start_date,end_date):
    ''' Input : Pass a list of stocks, start date and end date
    Output: Stock data including the daily returns data frame
    and  the risk measures'''

    # Input parameters
    tickers = ticker_list  # Example list of stock tickers
    start_date = start_date
    end_date = end_date

    # Fetch stock data
    stock_data = fetch_multiple_stock_data(tickers, start_date, end_date)

   # Calculate returns
    stock_data = calculate_returns(stock_data)

   # Calculate risk measures
    risk_measures = calculate_risk(stock_data)

    return stock_data

    # Print results
    print("Stock data summary:")
    #print(stock_data.head())
    #print("\nRisk measures:")
    #print(risk_measures)


In [4]:
stocks_data = stocks(['HDFCBANK.NS','TCS','INFY'],start_date='2020-01-01', end_date='2024-08-20')
stocks_data.head()

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed


Open         High          Low        Close    Adj Close  \
Date                                                                          
2020-01-01  1276.099976  1280.000000  1270.599976  1278.599976  1227.428589   
2020-01-02  1279.000000  1288.000000  1279.000000  1286.750000  1235.252441   
2020-01-03  1282.199951  1285.000000  1263.599976  1268.400024  1217.636841   
2020-01-06  1260.000000  1261.800049  1236.000000  1240.949951  1191.285400   
2020-01-07  1258.900024  1271.449951  1252.250000  1260.599976  1210.148926   

             Volume       Ticker  Daily_Returns  
Date                                             
2020-01-01  1836849  HDFCBANK.NS            NaN  
2020-01-02  3068583  HDFCBANK.NS       0.006374  
2020-01-03  5427775  HDFCBANK.NS      -0.014261  
2020-01-06  5445093  HDFCBANK.NS      -0.021641  
2020-01-07  7362247  HDFCBANK.NS       0.015835

In [5]:
#### Split the data into individual stocks

hdfc = stocks_data[stocks_data['Ticker']=='HDFCBANK.NS'].reset_index()
tcs = stocks_data[stocks_data['Ticker']=='TCS'].reset_index()
infosys = stocks_data[stocks_data['Ticker']=='INFY'].reset_index()

In [6]:
hdfc.describe()

Date         Open         High          Low  \
count                           1146  1146.000000  1146.000000  1146.000000   
mean   2022-04-21 17:30:28.272251392  1441.664441  1455.479754  1426.974260   
min              2020-01-01 00:00:00   770.450012   810.000000   738.750000   
25%              2021-02-22 06:00:00  1380.000000  1395.000000  1363.062531   
50%              2022-04-21 12:00:00  1491.125000  1506.274963  1479.375000   
75%              2023-06-15 18:00:00  1593.225037  1605.949951  1580.225037   
max              2024-08-19 00:00:00  1791.000000  1794.000000  1764.650024   
std                              NaN   201.932373   200.744924   204.178335   

             Close    Adj Close        Volume  Daily_Returns  
count  1146.000000  1146.000000  1.146000e+03    1145.000000  
mean   1441.337830  1402.470897  1.291993e+07       0.000403  
min     767.700012   736.975586  5.484040e+05      -0.126069  
25%    1377.324951  1331.357758  6.437438e+06      -0.007736  
50%    1491.525024  1447.983643  1.028824e+07       0.000621  
75%    1593.924957  1555.526337  1.687426e+07       0.008270  
max    1768.650024  1768.650024  8.670560e+07       0.115996  
std     202.460527   206.014400  9.424437e+06       0.017563

In [7]:
# group be ticker and compute the mean of the returns

stocks_data.groupby('Ticker').agg({'Daily_Returns':['mean','std','var']})


Daily_Returns                    
                     mean       std       var
Ticker                                       
HDFCBANK.NS      0.000403  0.017563  0.000308
INFY             0.000950  0.019500  0.000380
TCS              0.000326  0.058520  0.003425

# Probability basics, distributions-Binomial, Normal distributions

### Binomial Distribution

* Compute the monthly returns from HDFC stock data
* Flag as profit if  the returns is more than 5% (say) else loss
* Compute the number of months the stock has made profilt and loss

In [8]:

def compute_monthly_returns(prices_df):
  """
  This function takes a DataFrame containing adjusted daily closing prices
  with columns 'Date' and 'Adj Close' and computes monthly returns.

  Args:
      prices_df: DataFrame containing adjusted daily closing prices.

  Returns:
      A DataFrame with monthly returns.
  """

  # Ensure the 'Date' column is a datetime index
  prices_df['Date'] = pd.to_datetime(prices_df['Date'])
  prices_df.set_index('Date', inplace=True)
  prices_df = prices_df.drop(['Daily_Returns'],axis=1)
  # Resample data to monthly frequency, taking the end-of-month price
#   monthly_prices = prices_df['Adj Close'].resample('M').last()
  # monthly_prices =prices_df['Adj Close'].resample('M').agg(lambda x: (x + 1).prod() - 1)\
  # monthly_prices =prices_df['Adj Close'].asfreq('M').ffill()
  month_end_prices = prices_df.resample('BM').apply(lambda x: x[-1])
  month_end_prices['monthly_returns'] = month_end_prices['Adj Close'].pct_change()
  # Calculate monthly returns (percentage change)
  # monthly_returns = monthly_prices/monthly_prices.shift(1) -1

  return month_end_prices


In [9]:
hdfc_returns = compute_monthly_returns(hdfc).reset_index()
hdfc_returns.head()

<ipython-input-8-aa90d2d3d525>:21: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  month_end_prices = prices_df.resample('BM').apply(lambda x: x[-1])


Date         Open         High          Low        Close    Adj Close  \
0 2020-01-31  1231.449951  1237.800049  1220.250000  1226.300049  1177.221802   
1 2020-02-28  1175.500000  1185.000000  1170.099976  1177.650024  1130.518677   
2 2020-03-31   853.799988   873.599976   838.000000   861.900024   827.405579   
3 2020-04-30  1001.400024  1019.000000   992.099976  1001.799988   961.706543   
4 2020-05-29   944.000000   955.000000   923.450012   951.650024   913.563660   

     Volume       Ticker  monthly_returns  
0   5589134  HDFCBANK.NS              NaN  
1  12156528  HDFCBANK.NS        -0.039672  
2  17605546  HDFCBANK.NS        -0.268119  
3  21896567  HDFCBANK.NS         0.162316  
4  26512583  HDFCBANK.NS        -0.050060

In [10]:
# from the stock data calculate the monthly returns
profit_threshold = 0.05
hdfc_returns['profit_flag'] = hdfc_returns['monthly_returns'].apply(lambda x: 'Profit' if x > profit_threshold else 'Loss')
print('Counts: \n', hdfc_returns['profit_flag'].value_counts())
print('\n%\n',hdfc_returns['profit_flag'].value_counts(normalize=True))



Counts: 
 profit_flag
Loss      41
Profit    15
Name: count, dtype: int64

%
 profit_flag
Loss      0.732143
Profit    0.267857
Name: proportion, dtype: float64



* what is the probability of making a profit in a given month
* what is the probability of making profit of >5% twice a year
* what is the probability of making profit of >5% "atleast" twice a year


**Activity1:**
* What is the probability of making profit of >5% [0,1,2,... 12] times a year
* Cumulative probability


**Activity 2:**


Consider TCS stock and answer the following questions
* what is the probability of making a profit in a given month
* what is the probability of making profit of >5% twice a year
* what is the probability of making profit of >5% "atleast" twice a year


# Normal Distribution

#### Application of Normal distribution using PDF and CDF functions
* what is the probability of making a profit of 6% in a given year?
* what is the probability of making profit of 5% twice a year?
* what is the probability of making profit of >5%  in a given month?


**Activity 3:**
* What is the probability of hdfc stock closing price less than 1360
* What is the probability of hdfc stock closing price between 1400 to 1500
* What is the Probability of hdfc stock monthly returns being greater than 5% ?